## Set up

In [0]:
# %pip install -U -qqq langchain_core databricks_langchain langchain_community databricks-sql-connector databricks-sqlalchemy databricks-vectorsearch langchain-community
# %restart_python

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
grpcio-status 1.69.0 requires protobuf<6.0dev,>=5.26.1, but you have protobuf 4.25.8 which is incompatible.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql import functions as F

## EDA

In [0]:
%sql
SELECT * FROM `dais-hackathon-2025`.bright_initiative.airbnb_properties_information
WHERE
  -- location = 'Chicago, Illinois, United States'
  LOWER(location) LIKE '%new york%'
  AND host_number_of_reviews > 1000
  AND EXISTS(reviews, review -> review ILIKE '%wheelchair%')
LIMIT 5;

amenities arrangement_details availability available_dates breadcrumbs cancellation_policy category category_rating currency description description_by_sections description_html description_items details discount final_url guests highlights host_number_of_reviews host_rating host_response_rate hosts_year house_rules image images is_guest_favorite is_supperhost lat listing_name listing_title location location_details location_details_html long name pets_allowed price pricing_details property_id property_number_of_reviews ratings reviews seller_info total_price travel_details url List(List(Scenic views, List(List(Lake view, SYSTEM_VIEW_OCEAN))), List(Bathroom, List(List(Hair dryer, SYSTEM_HAIRDRYER), List(Hot water, SYSTEM_HOT_WATER))), List(Bedroom and laundry, List(List(Essentials, Towels, bed sheets, soap, and toilet paper), List(Hangers, SYSTEM_HANGERS), List(Iron, SYSTEM_IRON))), List(Entertainment, List(List(40-inch HDTV with standard cable, SYSTEM_TV))), List(Heating and cooling, List(List(AC – split-type ductless system, SYSTEM_SNOWFLAKE), List(Heating – split-type ductless system, SYSTEM_THERMOMETER))), List(Home safety, List(List(Exterior security cameras on property, Security cameras face the driveway and garage to ensure guests safety and privacy.), List(Smoke alarm, SYSTEM_DETECTOR_SMOKE), List(Carbon monoxide alarm, SYSTEM_DETECTOR_CO), List(Fire extinguisher, SYSTEM_FIRE_EXTINGUISHER), List(First aid kit, SYSTEM_FIRST_AID_KIT))), List(Internet and office, List(List(Wifi, SYSTEM_WI_FI))), List(Kitchen and dining, List(List(Kitchen, Space where guests can cook their own meals), List(Refrigerator, SYSTEM_REFRIGERATOR), List(Microwave, SYSTEM_MICROWAVE), List(Cooking basics, Pots and pans, oil, salt and pepper), List(Dishes and silverware, Bowls, chopsticks, plates, cups, etc.), List(Electric stove, SYSTEM_STOVE), List(Oven, SYSTEM_OVEN), List(Coffee maker, SYSTEM_COFFEE_MAKER))), List(Location features, List(List(Beach access – Beachfront, Guests can enjoy a nearby beach), List(Lake access, Guests can get to a lake using a path or dock), List(Private entrance, Separate street or building entrance))), List(Outdoor, List(List(Private patio or balcony, SYSTEM_PATIO_BALCONY), List(Shared backyard – Not fully fenced, An open space on the property usually covered in grass), List(Fire pit, SYSTEM_FIREPIT), List(Outdoor furniture, SYSTEM_ROOFTOP_DECK), List(Hammock, SYSTEM_HAMMOCK), List(Outdoor dining area, SYSTEM_ROOFTOP_DECK), List(BBQ grill, SYSTEM_GRILL))), List(Parking and facilities, List(List(Free parking on premises, SYSTEM_MAPS_CAR_RENTAL), List(EV charger, Guests can charge their electric vehicles on the property))), List(Services, List(List(Self check-in, SYSTEM_KEY), List(Keypad, Check yourself into the home with a door code))), List(Not included, List())) List(List(Bedroom 1, 1 queen bed), List(Bedroom 2, 1 queen bed)) true List(2025-04-22, 2025-04-23, 2025-04-27, 2025-04-28, 2025-04-29, 2025-04-30, 2025-05-03, 2025-05-04, 2025-05-05, 2025-05-06, 2025-05-07, 2025-05-11, 2025-05-12, 2025-05-13, 2025-05-14, 2025-05-16, 2025-05-17, 2025-05-18, 2025-05-19, 2025-05-20, 2025-05-21, 2025-05-22, 2025-05-23, 2025-05-24, 2025-05-25, 2025-05-26, 2025-05-27, 2025-05-28, 2025-05-29, 2025-06-01, 2025-06-02, 2025-06-03, 2025-06-04, 2025-06-08, 2025-06-09, 2025-06-10, 2025-06-11, 2025-06-12, 2025-06-15, 2025-06-23, 2025-06-24, 2025-06-27, 2025-06-28, 2025-07-03, 2025-07-04, 2025-07-05, 2025-07-13, 2025-07-28, 2025-07-29, 2025-07-30, 2025-07-31, 2025-08-05, 2025-08-06, 2025-08-07, 2025-08-08, 2025-08-09, 2025-08-10, 2025-08-11, 2025-08-12, 2025-08-13, 2025-08-14, 2025-08-15, 2025-08-18, 2025-08-19, 2025-08-20, 2025-08-25, 2025-08-26, 2025-08-27, 2025-08-28, 2025-09-01, 2025-09-02, 2025-09-03, 2025-09-04, 2025-09-05, 2025-09-06, 2025-09-07, 2025-09-08, 2025-09-09, 2025-09-10, 2025-09-11, 2025-09-12, 2025-09-13, 2025-09-14, 2025-09-15, 2025-09-16, 2025-09-17, 2025-09-22, 2025-09-23, 2025-09-24, 2025-09-25, 2025-09-26, 2025-09-27,

In [0]:
%sql
-- EDA
WITH t0 AS (
  SELECT property_id
  FROM `dais-hackathon-2025`.bright_initiative.airbnb_properties_information
  GROUP BY property_id
  HAVING COUNT(reviews) > 1 
)
SELECT 
t0.property_id
, t1.*
FROM workspace.acc.airbnb t1
INNER JOIN t0 ON t1.property_id = t0.property_id
ORDER BY t0.property_id


property_id id amenities arrangement_details availability available_dates breadcrumbs cancellation_policy category category_rating currency description description_by_sections description_html description_items details discount final_url guests highlights host_number_of_reviews host_rating host_response_rate hosts_year house_rules image images is_guest_favorite is_supperhost lat listing_name listing_title location location_details location_details_html long name pets_allowed price pricing_details property_id property_number_of_reviews ratings reviews seller_info total_price travel_details url 1000007051406614334 171798705941 List(List(Scenic views, List(List(Mountain view, SYSTEM_VIEW_MOUNTAIN), List(City skyline view, SYSTEM_VIEW_CITY))), List(Bathroom, List(List(Bathtub, SYSTEM_BATHTUB), List(Hair dryer, SYSTEM_HAIRDRYER), List(Cleaning products, SYSTEM_CLEANING_SUPPLIES), List(Shampoo, SYSTEM_SHAMPOO), List(Conditioner, SYSTEM_SHAMPOO), List(Body soap, SYSTEM_SOAP), List(Hot water, SYSTEM_HOT_WATER), List(Shower gel, SYSTEM_SOAP))), List(Bedroom and laundry, List(List(Free washer – In unit, SYSTEM_WASHER), List(Essentials, Towels, bed sheets, soap, and toilet paper), List(Hangers, SYSTEM_HANGERS), List(Bed linens, Cotton linens), List(Extra pillows and blankets, SYSTEM_PILLOW), List(Room-darkening shades, SYSTEM_BLACKOUT_SHADES), List(Iron, SYSTEM_IRON), List(Drying rack for clothing, SYSTEM_HANGERS), List(Clothing storage: closet and wardrobe, SYSTEM_WARDROBE))), List(Entertainment, List(List(Ethernet connection, SYSTEM_CABLE), List(50 inch HDTV with Chromecast, Netflix, SYSTEM_TV))), List(Heating and cooling, List(List(Central air conditioning, SYSTEM_SNOWFLAKE), List(Heating, SYSTEM_THERMOMETER))), List(Home safety, List(List(Fire extinguisher, SYSTEM_FIRE_EXTINGUISHER), List(First aid kit, SYSTEM_FIRST_AID_KIT))), List(Internet and office, List(List(Fast wifi – 101 Mbps, Verified by speed test. Stream 4K videos and join video calls on multiple devices.), List(Dedicated workspace, In a room with a door))), List(Kitchen and dining, List(List(Kitchen, Space where guests can cook their own meals), List(LG refrigerator, SYSTEM_REFRIGERATOR), List(Microwave, SYSTEM_MICROWAVE), List(Cooking basics, Pots and pans, oil, salt and pepper), List(Dishes and silverware, Bowls, chopsticks, plates, cups, etc.), List(Freezer, SYSTEM_REFRIGERATOR), List(Siemens double oven, SYSTEM_OVEN), List(Coffee maker: espresso machine, Nespresso, SYSTEM_COFFEE_MAKER), List(Wine glasses, SYSTEM_MAPS_BAR), List(Toaster, SYSTEM_TOASTER), List(Baking sheet, SYSTEM_BAKING_SHEET), List(Blender, SYSTEM_BLENDER), List(Dining table, SYSTEM_DINING_TABLE), List(Coffee, SYSTEM_COFFEE_MAKER))), List(Outdoor, List(List(Private patio or balcony, SYSTEM_PATIO_BALCONY), List(Outdoor furniture, SYSTEM_ROOFTOP_DECK), List(Outdoor dining area, SYSTEM_ROOFTOP_DECK))), List(Parking and facilities, List(List(Free street parking, SYSTEM_MAPS_CAR_RENTAL), List(Elevator, The home or building has an elevator that’s at least 52 inches deep and a doorway at least 32 inches wide), List(Paid parking garage off premises, SYSTEM_MAPS_CAR_RENTAL))), List(Services, List(List(Long term stays allowed, Allow stay for 28 days or more), List(Self check-in, SYSTEM_KEY), List(Lockbox, SYSTEM_SAFE), List(Cleaning available during stay, SYSTEM_CLEAN))), List(Not included, List())) List(List(Bedroom 1, 1 double bed), List(Bedroom 2, 1 queen bed), List(Living room, 1 sofa bed)) true List(2024-09-19, 2024-09-22, 2024-09-26, 2024-09-30, 2024-10-01, 2024-10-02, 2024-10-03, 2024-10-13, 2024-10-14, 2024-10-15, 2024-10-16, 2024-10-17, 2024-10-22, 2024-10-23, 2024-10-24, 2024-10-25, 2024-10-26, 2024-10-27, 2024-10-28, 2024-10-29, 2024-10-30, 2024-10-31, 2024-11-04, 2024-11-05, 2024-11-06, 2024-11-12, 2024-11-13, 2024-11-14, 2024-11-15, 2024-11-16, 2024-11-17, 2024-11-18, 2024-11-19, 2024-11-20, 2024-11-21, 2024-11-25, 2024-11-26, 2024-11-27, 2024-11-28, 2024-11-29, 2024-11-30, 2024-12-01, 2024-12-02, 

In [0]:
%sql
WITH raw AS (
SELECT 
  *
  , row_number() OVER (PARTITION BY property_id ORDER BY url DESC) AS instance
FROM `dais-hackathon-2025`.bright_initiative.airbnb_properties_information 
-- FROM workspace.acc.airbnb
WHERE property_id IS NOT NULL
-- AND EXISTS(reviws, review -> review ILIKE '%wheelchair%')
-- AND lower(location) LIKE '%new york%'
)
SELECT 
 property_id
 , concat_ws('\n', reviews) AS reviews
 , concat_ws('\n', CAST(amenities AS string)) AS amenities
 , concat_ws('\n', CAST(arrangement_details AS STRING)) AS arrangement_details 
 , description AS liting_description
 , concat_ws('\n', available_dates) AS available_dates
 , breadcrumbs
 , concat_ws('\n', cast(cancellation_policy as string)) AS cancellation_policy
 , category
 , concat_ws('\n', cast(category_rating as string)) AS category_ratings
 , currency
 , concat_ws('\n', description_items) AS description_iems
 , concat_ws('\n', details) AS details
 , discount
 , final_url
 , guests
 , concat_ws('\n', cast(highlights as string)) AS highlights
 , host_number_of_reviews
 , host_rating
 , host_response_rate
 , hosts_year
 , concat_ws('\n', house_rules) AS house_rules
 , is_guest_favorite
 ,is_supperhost
 , lat
 , listing_name
 , listing_title
 , location
 , long
 , name
 , pets_allowed
 , price
 , concat_ws('\n', cast(pricing_details as string)) AS pricing_details
 , property_number_of_reviews AS number_of_reviews
 , ratings
 , total_price
  -- ,*
FROM raw
WHERE instance = 1
LIMIT 100

property_id reviews amenities arrangement_details liting_description available_dates breadcrumbs cancellation_policy category category_ratings currency description_iems details discount final_url guests highlights host_number_of_reviews host_rating host_response_rate hosts_year house_rules is_guest_favorite is_supperhost lat listing_name listing_title location long name pets_allowed price pricing_details number_of_reviews ratings total_price 1000063164808270072 Great place to stay, near all the beaches. The apt was very clean and Sharon was very nice host. We will comeback
There is no Sharon amazing hospitality highly and lovingly clean house everything is close to everything good location comes home there is quiet when you want and when you want to go out just walk and everything is close to everything recommend it and come back again there is a very good pool and everything is clean and amazing service
The stay was very pleasant, the apartment is fully equipped for a short and long stay, clean and tidy as in the pictures, winning location.
Great location, luxurious complex and a pool. Feels like a hotel on the boardwalk
Sharon is lovely, pleasant and always available with a great attitude. Great apartment, clean, cozy and furnished at a high level just like in the pictures and even more. A quiet and beautiful seaside complex, quiet corners in the pool and a great attitude from the workers.
The unit is in a new building,guard at the entrance, clean and tidy. Prime location A few minutes walk to the sea to the mall and the promenade. The unit itself looks exactly as pictured. Accurate equipped everything was clean and spotless and new . Communication with the host Sharon was great provided us with all the information we needed and was available. Thank you so much! We look forward to coming back
It was great,clean and Sharon was very nice
A stunning place gives a high level of luxurious and luxurious feel [{Bedroom and laundry, [{Hangers, SYSTEM_HANGERS}, {Bed linen, SYSTEM_BLANKETS}, {Extra pillows and blankets, SYSTEM_PILLOW}, {Black-out blinds, SYSTEM_BLACKOUT_SHADES}, {Iron, SYSTEM_IRON}, {Clothing storage, SYSTEM_WARDROBE}]}, {Entertainment, [{TV, SYSTEM_TV}]}, {Heating and cooling, [{Air conditioning, SYSTEM_SNOWFLAKE}, {Heating, SYSTEM_THERMOMETER}]}, {Home safety, [{Exterior security cameras on property, The outside perimeter features security cameras.
Of course there are no cameras in the apartment itself.}, {Smoke alarm, SYSTEM_DETECTOR_SMOKE}, {Fire extinguisher, SYSTEM_FIRE_EXTINGUISHER}]}, {Internet and office, [{Wi-Fi, SYSTEM_WI_FI}]}, {Kitchen and dining, [{Kitchen, Space where guests can cook their own meals}, {Refrigerator, SYSTEM_REFRIGERATOR}, {Microwave, SYSTEM_MICROWAVE}, {Dishes and cutlery, Bowls, chopsticks, plates, cups, etc.}, {Freezer, SYSTEM_REFRIGERATOR}, {Stove, SYSTEM_STOVE}, {Oven, SYSTEM_OVEN}, {Hot water kettle, SYSTEM_WATER_KETTLE}, {Coffee maker, SYSTEM_COFFEE_MAKER}, {Wine glasses, SYSTEM_MAPS_BAR}, {Toaster, SYSTEM_TOASTER}, {Baking sheet, SYSTEM_BAKING_SHEET}, {Coffee, SYSTEM_COFFEE_MAKER}]}, {Location features, [{Beach access – Beachfront, Guests can enjoy a nearby beach}]}, {Parking and facilities, [{Free parking on premises, SYSTEM_MAPS_CAR_RENTAL}, {Shared pool, SYSTEM_POOL}]}, {Services, [{Self check-in, SYSTEM_KEY}, {Key Safe, SYSTEM_SAFE}]}, {Not included, []}] [{Bedroom, 1 double bed, 2 sofa beds}] Holiday apartment in a new and prestigious complex ' sea side' in EilatThe complex includes:◇ a sheltered space.◇Security 24/7.◇Synagogue.Shabbos ◇elevator.◇Pool.Fully equipped and kosher◇ kitchen.A pampering◇ bedroom.◇ Two sofas open to a double bed.◇Internet.◇A variety of TV channels.Winning ◇location.◇ 2 minutes from the sea ( adjacent to the Club Hotel).Eilat ◇promenade across the road.The spaceThe apartment has one bedroom, which includes a wardrobe, a double bed, a TV dresser, a TV with channels.In addition to the apartment there is a niche with a double sofa bed.The living room ha

In [0]:
%sql
USE CATALOG workspace;
USE SCHEMA sql;

DROP TABLE IF EXISTS airbnb_property; 
CREATE OR REPLACE TABLE airbnb_property
AS
WITH raw AS (
SELECT 
  *
  , row_number() OVER (PARTITION BY property_id ORDER BY url DESC) AS instance
FROM `dais-hackathon-2025`.bright_initiative.airbnb_properties_information 
-- FROM workspace.acc.airbnb
WHERE property_id IS NOT NULL
-- AND EXISTS(reviws, review -> review ILIKE '%wheelchair%')
-- AND lower(location) LIKE '%new york%'
)
SELECT 
 property_id
 , concat_ws('\n', reviews) AS reviews
 , concat_ws('\n', CAST(amenities AS string)) AS amenities
 , concat_ws('\n', CAST(arrangement_details AS STRING)) AS arrangement_details 
 , description AS liting_description
 , concat_ws('\n', available_dates) AS available_dates
 , breadcrumbs
 , concat_ws('\n', cast(cancellation_policy as string)) AS cancellation_policy
 , category
 , concat_ws('\n', cast(category_rating as string)) AS category_ratings
 , currency
 , concat_ws('\n', description_items) AS description_iems
 , concat_ws('\n', details) AS details
 , discount
 , final_url
 , guests
 , concat_ws('\n', cast(highlights as string)) AS highlights
 , host_number_of_reviews
 , host_rating
 , host_response_rate
 , hosts_year
 , concat_ws('\n', house_rules) AS house_rules
 , is_guest_favorite
 ,is_supperhost
 , lat
 , listing_name
 , listing_title
 , location
 , long
 , name
 , pets_allowed
 , price
 , concat_ws('\n', cast(pricing_details as string)) AS pricing_details
 , property_number_of_reviews AS number_of_reviews
 , ratings
 , total_price
FROM raw
WHERE instance = 1

num_affected_rows num_inserted_rows

In [0]:
df = spark.sql("SELECT * FROM workspace.sql.airbnb_property LIMIT 10")
display(df)

property_id reviews amenities arrangement_details liting_description available_dates breadcrumbs cancellation_policy category category_ratings currency description_iems details discount final_url guests highlights host_number_of_reviews host_rating host_response_rate hosts_year house_rules is_guest_favorite is_supperhost lat listing_name listing_title location long name pets_allowed price pricing_details number_of_reviews ratings total_price 1000077622157753133 Great house at a great location. Rooms are spacious. The fenced- in yard is perfect size. Garage access was greatly appreciated, especially during the snowfall. Jason was very responsive with questions. He did snow removal even on days where temperatures were frigid. Amazing host! Will definitely recommend!
Very responsive host, the place was great. Highly recommended and gonna stop by again while visiting Omaha! [{Scenic views, [{Courtyard view, SYSTEM_FLOWER}]}, {Bathroom, [{Bathtub, SYSTEM_BATHTUB}, {Hair dryer, SYSTEM_HAIRDRYER}, {Cleaning products, SYSTEM_CLEANING_SUPPLIES}, {Shampoo, SYSTEM_SHAMPOO}, {Conditioner, SYSTEM_SHAMPOO}, {Body soap, SYSTEM_SOAP}, {Hot water, SYSTEM_HOT_WATER}, {Shower gel, SYSTEM_SOAP}]}, {Bedroom and laundry, [{Free washer – In unit, SYSTEM_WASHER}, {Free dryer – In unit, SYSTEM_DRYER}, {Essentials, Towels, bed sheets, soap, and toilet paper}, {Hangers, SYSTEM_HANGERS}, {Bed linens, Cotton linens}, {Room-darkening shades, SYSTEM_BLACKOUT_SHADES}, {Iron, SYSTEM_IRON}, {Clothing storage: closet, SYSTEM_WARDROBE}]}, {Entertainment, [{Ethernet connection, SYSTEM_CABLE}, {50 inch HDTV with Amazon Prime Video, SYSTEM_TV}]}, {Family, [{Pack ’n play/Travel crib - always at the listing, SYSTEM_PACK_N_PLAY}, {Children’s dinnerware, SYSTEM_CHILD_UTENSILS}, {Outlet covers, SYSTEM_OUTLET_COVER}]}, {Heating and cooling, [{Central air conditioning, SYSTEM_SNOWFLAKE}, {Ceiling fan, SYSTEM_FAN_CEILING}, {Portable fans, SYSTEM_FAN_PORTABLE}, {Central heating, SYSTEM_THERMOMETER}]}, {Home safety, [{Exterior security cameras on property, WYZE DOORBELL CAMERA / DRIVEWAY CAMERA INSTALLED}, {Smoke alarm, SYSTEM_DETECTOR_SMOKE}, {Carbon monoxide alarm, SYSTEM_DETECTOR_CO}, {Fire extinguisher, SYSTEM_FIRE_EXTINGUISHER}, {First aid kit, SYSTEM_FIRST_AID_KIT}]}, {Internet and office, [{Wifi, SYSTEM_WI_FI}, {Dedicated workspace, In a room with a door}]}, {Kitchen and dining, [{Kitchen, Space where guests can cook their own meals}, {Refrigerator, SYSTEM_REFRIGERATOR}, {Microwave, SYSTEM_MICROWAVE}, {Cooking basics, Pots and pans, oil, salt and pepper}, {Dishes and silverware, Bowls, chopsticks, plates, cups, etc.}, {Freezer, SYSTEM_REFRIGERATOR}, {Dishwasher, SYSTEM_DISHWASHER}, {KitchenAid electric stove, SYSTEM_STOVE}, {Stainless steel single oven, SYSTEM_OVEN}, {Hot water kettle, SYSTEM_WATER_KETTLE}, {Coffee maker, SYSTEM_COFFEE_MAKER}, {Wine glasses, SYSTEM_MAPS_BAR}, {Toaster, SYSTEM_TOASTER}, {Baking sheet, SYSTEM_BAKING_SHEET}, {Blender, SYSTEM_BLENDER}, {Barbecue utensils, Grill, charcoal, bamboo skewers/iron skewers, etc.}, {Dining table, SYSTEM_DINING_TABLE}, {Coffee, SYSTEM_COFFEE_MAKER}]}, {Location features, [{Private entrance, Separate street or building entrance}, {Laundromat nearby, SYSTEM_LAUNDRY_SERVICE}]}, {Outdoor, [{Private patio or balcony, SYSTEM_PATIO_BALCONY}, {Private backyard – Fully fenced, An open space on the property usually covered in grass}, {Outdoor furniture, SYSTEM_ROOFTOP_DECK}, {Outdoor dining area, SYSTEM_ROOFTOP_DECK}, {Private BBQ grill: gas, SYSTEM_GRILL}]}, {Parking and facilities, [{Free parking on premises, SYSTEM_MAPS_CAR_RENTAL}, {Free street parking, SYSTEM_MAPS_CAR_RENTAL}]}, {Services, [{Pets allowed, Assistance animals are always allowed}, {Luggage dropoff allowed, For guests' convenience when they have early arrival or late departure}, {Long term stays allowed, Allow stay for 28 days or more}, {Self check-in, SYSTEM_KEY}, {Smart lock, SYSTEM_LOCK_ON_DOOR}]}] [{Bedroom 1, 1 king bed}, {Bedroom 2, 1 king bed}, {Bed

## SQL Tool

In [0]:
import ast
import re

from langchain.chains import create_sql_query_chain
from langchain_community.tools import QuerySQLDataBaseTool  ## Updated
from langchain_community.utilities import SQLDatabase
# from databricks.vector_search.client import VectorSearchClient
# from langchain_community.vectorstores import DatabricksVectorSearch
from databricks_langchain import DatabricksVectorSearch  ## Updated
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnableParallel, RunnablePassthrough
from databricks_langchain import ChatDatabricks
from databricks.sdk import WorkspaceClient
import os
import mlflow

In [0]:

mlflow.langchain.autolog(silent=True)

w = WorkspaceClient()

os.environ["DATABRICKS_HOST"] = w.config.host
os.environ["DATABRICKS_TOKEN"] = w.tokens.create(comment="for model serving", lifetime_seconds=1200).token_value
os.environ["DATABRICKS_HOSTNAME"] = "dbc-581b2c6f-8577.cloud.databricks.com"
# os.environ["DATABRICKS_HOST"] = "https://dbc-eebd97f8-a4cd.cloud.databricks.com"
print(os.environ["DATABRICKS_HOST"])

https://dbc-581b2c6f-8577.cloud.databricks.com


In [0]:
def query_sql_airbnb(input):
    
    system = """You are a SQL expert and acting as a preliminary filter to table workspace.acc.airbnb_property\
    given an input question return only relevant property_id values which could relate to the question.\
    Create a syntactically correct SQL query to run with no mark up or explanation. \
    Unless otherwise specified, do not return more than 50 rows or {top_k} if requested.

    Your main task is to filter and only return the property_id column. Do not perform any aggregation \
    (like COUNT, DISTINCT COUNT, SUM, etc.) or sorting and merging with other tables, just use SELECT property_id \
    FROM workspace.acc.airbnb_property WHERE... If the input question ask you to perform other tasks rather than just filtering \
    the data, you can ignore all of these other tasks, and just return the filtered ProjectID values, DO NOT RETURN \
    any other columns in your SQL query. DO NOT make any DML statements (INSERT, UPDATE, DELETE, DROP etc.) to the database.
    Only use the following tables info: {table_info}

    When searching for disabilities or wheelchair accessible in review, try filter the data with column `reviews` and search by matching '%wheelchair%' or '%wheel chair%'

    Below are some example questions and their expected SQL queries output. Only return the SQL query with no markup or explanation.

    User input: find listing with ratings more than 4 in New York for people with disabilities or wheelchair accessible
    SQL query: SELECT property_id FROM workspace.acc.airbnb_property \
    WHERE rating >= 4 \
    AND (reviews LIKE ''wheelchair%'' OR reviews LIKE ''wheel chair%'')
    AND (location LIKE '%new york%' OR location LIKE '%new york%')

    User input: {input}
    SQL query:
    """

    ## Get table info
    db = SQLDatabase.from_databricks(
        catalog="workspace",
        schema="sql",
        engine_args={"pool_pre_ping": True},
        host=os.environ.get("DATABRICKS_HOSTNAME"),
        api_token=os.environ.get("DATABRICKS_TOKEN"),
        warehouse_id="e6d1b4d027dab190",  # sql-warehouse
    )

    def get_table_info(input):
        return db.get_table_info({"airbnb_property"})

    def query_database(query):
        try:
            res = db.run(query)
        except Exception as e:
            return "Could not execute query: {}".format(e)
        res = [el for sub in ast.literal_eval(res) for el in sub if el]
        res = [re.sub(r"\b\d+\b", "", string).strip() for string in res]
        return ", ".join(res)

    sql_prompt = ChatPromptTemplate.from_messages(
                [("system", system), ("human", "{input}")]
            )

    llm = ChatDatabricks(
        endpoint="databricks-meta-llama-3-3-70b-instruct", 
        temperature=0,
        target_uri="databricks",
    )

    write_query = create_sql_query_chain(llm, db, prompt=sql_prompt)
    execute_query = QuerySQLDataBaseTool(db=db)
    # execute_query = QuerySQLDataBaseTool(db=db)


    custom_chain = (
                {
                    "input": RunnablePassthrough()
                }
                | RunnablePassthrough().assign(filter_sql_id=(
                RunnableParallel(
                    {
                        "question": RunnablePassthrough() | (lambda x: x["input"]),
                        "table_info": get_table_info,
                    }
                )
                | write_query
                | execute_query
            )
        )
    )

    return custom_chain.invoke(input)


test_query = "find listing in New York for people with disabilities"
query_sql_airbnb(test_query)

{'input': 'find listing in New York for people with disabilities',
 'filter_sql_id': 'Error: (databricks.sql.exc.ServerOperationError) [DATATYPE_MISMATCH.UNEXPECTED_INPUT_TYPE] Cannot resolve "reviews LIKE %wheelchair%" due to data type mismatch: The first parameter requires the "STRING" type, however "reviews" has the type "ARRAY<STRING>". SQLSTATE: 42K09; line 1 pos 69\n[SQL: SELECT property_id FROM workspace.acc.airbnb_property WHERE (reviews LIKE \'%wheelchair%\' OR reviews LIKE \'%wheel chair%\') AND (location LIKE \'%new york%\' OR location LIKE \'%new york%\')]\n(Background on this error at: https://sqlalche.me/e/20/4xp6)'}

Trace(request_id=tr-0760c299d3b04a8ba9c5228b9464159c)